# Capstone Project - The Battle of Neighborhoods (Week 1-2)


##  Introduction/Business Problem

### Background


According to Bloomberg News, the London Housing Market is in a rut. It is now facing a number of different headwinds, including the prospect of higher taxes and a warning from the Bank of England that U.K. home values could fall as much as 30 percent in the event of a disorderly exit from the European Union. More specifically, four overlooked cracks suggest that the London market may be in worse shape than many realize: hidden price falls, record-low sales, homebuilder exodus and tax hikes addressing overseas buyers of homes in England and Wales.

### Business Problem

In this scenario, it is urgent to adopt machine learning tools in order to assist homebuyers clientele in London to make wise and effective decisions. As a result, the business problem we are currently posing is: how could we provide support to homebuyers clientele in to purchase a suitable real estate in London in this uncertain economic and financial scenario?



To solve this business problem, we are going to cluster London neighborhoods in order to recommend venues and the current average price of real estate where homebuyers can make a real estate investment. We will recommend profitable venues according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores.



## Data

Data on London properties and the relative price paid data were extracted from the HM Land Registry (http://landregistry.data.gov.uk/). The following fields comprise the address data included in Price Paid Data: Postcode; PAON Primary Addressable Object Name. Typically the house number or name; SAON Secondary Addressable Object Name. If there is a sub-building, for example, the building is divided into flats, there will be a SAON; Street; Locality; Town/City; District; County.

To explore and target recommended locations across different venues according to the presence of amenities and essential facilities, we will access data through FourSquare API interface and arrange them as a dataframe for visualization. By merging data on London properties and the relative price paid data from the HM Land Registry and data on amenities and essential facilities surrounding such properties from FourSquare API interface, we will be able to recommend profitable real estate investments.


### Methodology 

Below are the main components of our analysis and predication system.

1. Collect Inspection Data
2. Explore and Understand Data
3. Data preparation and preprocessing 
4. Modeling

#### 1. Collect Inspection Data

In [8]:
import os # Operating System
import numpy as np
import pandas as pd
import datetime as dt # Datetime
import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

#!conda install -c conda-forge folium=0.5.0 --yes
import folium #import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    ------------------------------------------------------------
                                           Total:          90 KB

The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0   conda-forge
    geopy:         1.20.0-py_0 conda-forge


geographiclib-1.49   | 32 KB     | ##################################### | 100% 
geopy-1.20.0         | 57 KB     | ##################################### | 100% 
Preparing transaction: done
Verifying transaction: done
Executing transaction: done
Libraries imported.


Now let's download and explore the data

In [9]:
#Read the data for examination (Source: http://landregistry.data.gov.uk/)
df_ppd = pd.read_csv("http://prod2.publicdata.landregistry.gov.uk.s3-website-eu-west-1.amazonaws.com/pp-2018.csv")


df_ppd.head(5)

{666758D7-43A9-3363-E053-6B04A8C0D74E}  405000  2018-01-25 00:00  WR15 8LH  \
0  {666758D7-43AA-3363-E053-6B04A8C0D74E}  315000  2018-01-23 00:00   SY7 8QA   
1  {666758D7-43AD-3363-E053-6B04A8C0D74E}  165000  2018-01-19 00:00   SY1 2BF   
2  {666758D7-43B0-3363-E053-6B04A8C0D74E}  370000  2018-01-22 00:00   SY8 4DF   
3  {666758D7-43B3-3363-E053-6B04A8C0D74E}  320000  2018-01-19 00:00  TF10 7ET   
4  {666758D7-43B4-3363-E053-6B04A8C0D74E}  180000  2018-01-31 00:00   SY3 0NQ   

   D  N  F RAMBLERS WAY Unnamed: 8        Unnamed: 9          BORASTON  \
0  D  N  F  MONT CENISE        NaN               NaN              CLUN   
1  T  Y  F           42        NaN        PENSON WAY               NaN   
2  D  N  F   WILLOW HEY        NaN               NaN  ASHFORD CARBONEL   
3  D  N  F            3        NaN  PRINCESS GARDENS               NaN   
4  S  N  F           79        NaN     LYTHWOOD ROAD      BAYSTON HILL   

  TENBURY WELLS  SHROPSHIRE SHROPSHIRE.1  A A.1  
0   CRAVEN ARMS  SHROPSHIRE   SHROPSHIRE  A   A  
1    SHREWSBURY  SHROPSHIRE   SHROPSHIRE  A   A  
2        LUDLOW  SHROPSHIRE   SHROPSHIRE  A   A  
3       NEWPORT      WREKIN       WREKIN  A   A  
4    SHREWSBURY  SHROPSHIRE   SHROPSHIRE  A   A

In [10]:
df_ppd.shape


(1021214, 16)

Our dataset consists of over 1020000 rows and 16 columns. We will now prepare and preprocess data accordingly.

#### 3. Data preparation and preprocessing 

At this stage, we prepare our dataset for the modeling process, opting for the most suitable machine learning algorithm for our scope. 
Accordingly, we perform the following steps:

 Rename the column names, 
 Format the date column, 
 Sort data by date of sale, 
 Select data only for the city of London, 
 Make a list of street names in London, 
 Calculate the street-wise average price of the property, 
 Read the street-wise coordinates into a data frame, eliminating recurring word London from individual names, 
 Join the data to find the coordinates of locations which fit into client's budget, 
 Plot recommended locations on London map along with current market prices.

In [11]:
# Assign meaningful column names
df_ppd.columns = ['TUID', 'Price', 'Date_Transfer', 'Postcode', 'Prop_Type', 'Old_New', 'Duration', 'PAON', \
                  'SAON', 'Street', 'Locality', 'Town_City', 'District', 'County', 'PPD_Cat_Type', 'Record_Status']

# Format the date column
df_ppd['Date_Transfer'] = df_ppd['Date_Transfer'].apply(pd.to_datetime)

# Delete all obsolete transactions which were done before 2016
df_ppd.drop(df_ppd[df_ppd.Date_Transfer.dt.year < 2016].index, inplace=True)

# Sort by Date of Sale
df_ppd.sort_values(by=['Date_Transfer'],ascending=[False],inplace=True)

df_ppd_london = df_ppd.query("Town_City == 'LONDON'")

# Make a list of street names in LONDON
streets = df_ppd_london['Street'].unique().tolist()

df_grp_price = df_ppd_london.groupby(['Street'])['Price'].mean().reset_index()

# Give meaningful names to the columns
df_grp_price.columns = ['Street', 'Avg_Price']

#Input your Budget's Upper Limit and Lower Limit - Find the locations df_grp_price which fits your budget
df_affordable = df_grp_price.query("(Avg_Price >= 2200000) & (Avg_Price <= 2500000)")


# Display the dataframe
df_affordable

Street     Avg_Price
196                ALBION SQUARE  2.450000e+06
391                  ANHALT ROAD  2.435000e+06
406              ANSDELL TERRACE  2.250000e+06
421              APPLEGARTH ROAD  2.400000e+06
699             AYLESTONE AVENUE  2.286667e+06
853              BARONSMEAD ROAD  2.375000e+06
979               BEAUCLERC ROAD  2.480000e+06
1100             BELVEDERE DRIVE  2.340000e+06
1213           BICKENHALL STREET  2.208500e+06
1251           BIRCHLANDS AVENUE  2.217000e+06
1550              BRAMPTON GROVE  2.456875e+06
1629           BRIARDALE GARDENS  2.397132e+06
1794                    BROOKWAY  2.400000e+06
1911                BURBAGE ROAD  2.445000e+06
1977                   BURY WALK  2.492500e+06
2064             CALLCOTT STREET  2.375000e+06
2125           CAMPDEN HILL ROAD  2.379653e+06
2132                CAMPION ROAD  2.461000e+06
2155               CANNING PLACE  2.425000e+06
2222               CARLISLE ROAD  2.200000e+06
2227             CARLTON GARDENS  2.483500e+06
2239               CARLYLE COURT  2.300000e+06
2402              CHALCOT SQUARE  2.286679e+06
2480                CHARLES LANE  2.414000e+06
2558            CHELSEA CRESCENT  2.495000e+06
2602         CHESTER CLOSE NORTH  2.450000e+06
2633                CHEYNE COURT  2.250000e+06
2636                  CHEYNE ROW  2.410000e+06
2681               CHISWICK MALL  2.287500e+06
2756                   CITY ROAD  2.468340e+06
2803            CLARENDON STREET  2.250000e+06
2894            CLONCURRY STREET  2.388333e+06
2938                COLBECK MEWS  2.367500e+06
3196       CORNWALL TERRACE MEWS  2.350000e+06
3249          COURT LANE GARDENS  2.360000e+06
3371              CRESCENT GROVE  2.298000e+06
3577               DALEBURY ROAD  2.400000e+06
3843               DEWHURST ROAD  2.425000e+06
3924                  DORIA ROAD  2.362500e+06
3975              DOWNSHIRE HILL  2.225000e+06
4030                DUCHESS WALK  2.477500e+06
4226       ECCLESTON SQUARE MEWS  2.335500e+06
4279               EGBERT STREET  2.265000e+06
4283               EGERTON PLACE  2.200000e+06
4368               ELM PARK ROAD  2.320425e+06
5006             FRANK DIXON WAY  2.212500e+06
5088                 FULTON MEWS  2.299000e+06
5231                 GERARD ROAD  2.258500e+06
5234                GERRARD ROAD  2.242500e+06
5279               GIRDLERS ROAD  2.441667e+06
5372         GLOUCESTER CRESCENT  2.350833e+06
5440                GORDON PLACE  2.477000e+06
5476              GRAFTON SQUARE  2.270000e+06
5483              GRAHAM TERRACE  2.325000e+06
5941                HARMAN DRIVE  2.262500e+06
5965               HARRIS STREET  2.471769e+06
6027             HAVANNAH STREET  2.217309e+06
6098              HAZLEWELL ROAD  2.500000e+06
6214               HEREFORD MEWS  2.310000e+06
6234            HERONDALE AVENUE  2.475000e+06
6331        HIGHGATE HIGH STREET  2.211000e+06
6346               HIGHWOOD HILL  2.252500e+06
6382              HILLGATE PLACE  2.200000e+06
6491           HOLLYCROFT AVENUE  2.361375e+06
6495              HOLLYWOOD MEWS  2.350000e+06
6541              HONEYWELL ROAD  2.278333e+06
6597              HORTENSIA ROAD  2.275917e+06
6626               HOXTON SQUARE  2.234286e+06
6652                 HUNTER ROAD  2.300000e+06
6810               JACKSONS LANE  2.362500e+06
6870                 JOHN STREET  2.235000e+06
7174            KINNERTON STREET  2.485600e+06
7208         KNARESBOROUGH PLACE  2.325000e+06
7228                 KNOX STREET  2.250000e+06
7248              LADBROKE GROVE  2.483300e+06
7317              LANCASTER MEWS  2.312500e+06
7387              LANSDOWNE ROAD  2.429871e+06
7414   LATIMER INDUSTRIAL ESTATE  2.400000e+06
7467                LAXTON PLACE  2.500000e+06
7666              LINCOLN AVENUE  2.203500e+06
7694              LINGFIELD ROAD  2.248750e+06
7723               LISSON STREET  2.462500e+06
7757             LIVERPOOL GROVE  2.288000e+06
7849              LONGWOOD DRIVE  2.375000e+06
7855             LONSDALE SQUAR

In [12]:
geolocator = Nominatim()
df_affordable['city_coord'] = df_affordable['Street'].apply(geolocator.geocode).apply(lambda x: (x.latitude, x.longitude))
df_affordable

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  if __name__ == '__main__':
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


Street     Avg_Price  \
196                ALBION SQUARE  2.450000e+06   
391                  ANHALT ROAD  2.435000e+06   
406              ANSDELL TERRACE  2.250000e+06   
421              APPLEGARTH ROAD  2.400000e+06   
699             AYLESTONE AVENUE  2.286667e+06   
853              BARONSMEAD ROAD  2.375000e+06   
979               BEAUCLERC ROAD  2.480000e+06   
1100             BELVEDERE DRIVE  2.340000e+06   
1213           BICKENHALL STREET  2.208500e+06   
1251           BIRCHLANDS AVENUE  2.217000e+06   
1550              BRAMPTON GROVE  2.456875e+06   
1629           BRIARDALE GARDENS  2.397132e+06   
1794                    BROOKWAY  2.400000e+06   
1911                BURBAGE ROAD  2.445000e+06   
1977                   BURY WALK  2.492500e+06   
2064             CALLCOTT STREET  2.375000e+06   
2125           CAMPDEN HILL ROAD  2.379653e+06   
2132                CAMPION ROAD  2.461000e+06   
2155               CANNING PLACE  2.425000e+06   
2222               CARLISLE ROAD  2.200000e+06   
2227             CARLTON GARDENS  2.483500e+06   
2239               CARLYLE COURT  2.300000e+06   
2402              CHALCOT SQUARE  2.286679e+06   
2480                CHARLES LANE  2.414000e+06   
2558            CHELSEA CRESCENT  2.495000e+06   
2602         CHESTER CLOSE NORTH  2.450000e+06   
2633                CHEYNE COURT  2.250000e+06   
2636                  CHEYNE ROW  2.410000e+06   
2681               CHISWICK MALL  2.287500e+06   
2756                   CITY ROAD  2.468340e+06   
2803            CLARENDON STREET  2.250000e+06   
2894            CLONCURRY STREET  2.388333e+06   
2938                COLBECK MEWS  2.367500e+06   
3196       CORNWALL TERRACE MEWS  2.350000e+06   
3249          COURT LANE GARDENS  2.360000e+06   
3371              CRESCENT GROVE  2.298000e+06   
3577               DALEBURY ROAD  2.400000e+06   
3843               DEWHURST ROAD  2.425000e+06   
3924                  DORIA ROAD  2.362500e+06   
3975              DOWNSHIRE HILL  2.225000e+06   
4030                DUCHESS WALK  2.477500e+06   
4226       ECCLESTON SQUARE MEWS  2.335500e+06   
4279               EGBERT STREET  2.265000e+06   
4283               EGERTON PLACE  2.200000e+06   
4368               ELM PARK ROAD  2.320425e+06   
5006             FRANK DIXON WAY  2.212500e+06   
5088                 FULTON MEWS  2.299000e+06   
5231                 GERARD ROAD  2.258500e+06   
5234                GERRARD ROAD  2.242500e+06   
5279               GIRDLERS ROAD  2.441667e+06   
5372         GLOUCESTER CRESCENT  2.350833e+06   
5440                GORDON PLACE  2.477000e+06   
5476              GRAFTON SQUARE  2.270000e+06   
5483              GRAHAM TERRACE  2.325000e+06   
5941                HARMAN DRIVE  2.262500e+06   
5965               HARRIS STREET  2.471769e+06   
6027             HAVANNAH STREET  2.217309e+06   
6098              HAZLEWELL ROAD  2.500000e+06   
6214               HEREFORD MEWS  2.310000e+06   
6234            HERONDALE AVENUE  2.475000e+06   
6331        HIGHGATE HIGH STREET  2.211000e+06   
6346               HIGHWOOD HILL  2.252500e+06   
6382              HILLGATE PLACE  2.200000e+06   
6491           HOLLYCROFT AVENUE  2.361375e+06   
6495              HOLLYWOOD MEWS  2.350000e+06   
6541              HONEYWELL ROAD  2.278333e+06   
6597              HORTENSIA ROAD  2.275917e+06   
6626               HOXTON SQUARE  2.234286e+06   
6652                 HUNTER ROAD  2.300000e+06   
6810               JACKSONS LANE  2.362500e+06   
6870                 JOHN STREET  2.235000e+06   
7174            KINNERTON STREET  2.485600e+06   
7208         KNARESBOROUGH PLACE  2.325000e+06   
7228                 KNOX STREET  2.250000e+06   
7248              LADBROKE GROVE  2.483300e+06   
7317              LANCASTER MEWS  2.312500e+06   
7387              LANSDOWNE ROAD  2.429871e+06   
7414   LATIMER INDUSTRIAL ESTATE  2.400000e+06   
7467                LAXTON PLACE  2.500000e+06   
7666              LINCOLN 

In [13]:
df_affordable[['Latitude', 'Longitude']] = df_affordable['city_coord'].apply(pd.Series)
df_affordable

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:3391: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self[k1] = value[k2]


Street     Avg_Price  \
196                ALBION SQUARE  2.450000e+06   
391                  ANHALT ROAD  2.435000e+06   
406              ANSDELL TERRACE  2.250000e+06   
421              APPLEGARTH ROAD  2.400000e+06   
699             AYLESTONE AVENUE  2.286667e+06   
853              BARONSMEAD ROAD  2.375000e+06   
979               BEAUCLERC ROAD  2.480000e+06   
1100             BELVEDERE DRIVE  2.340000e+06   
1213           BICKENHALL STREET  2.208500e+06   
1251           BIRCHLANDS AVENUE  2.217000e+06   
1550              BRAMPTON GROVE  2.456875e+06   
1629           BRIARDALE GARDENS  2.397132e+06   
1794                    BROOKWAY  2.400000e+06   
1911                BURBAGE ROAD  2.445000e+06   
1977                   BURY WALK  2.492500e+06   
2064             CALLCOTT STREET  2.375000e+06   
2125           CAMPDEN HILL ROAD  2.379653e+06   
2132                CAMPION ROAD  2.461000e+06   
2155               CANNING PLACE  2.425000e+06   
2222               CARLISLE ROAD  2.200000e+06   
2227             CARLTON GARDENS  2.483500e+06   
2239               CARLYLE COURT  2.300000e+06   
2402              CHALCOT SQUARE  2.286679e+06   
2480                CHARLES LANE  2.414000e+06   
2558            CHELSEA CRESCENT  2.495000e+06   
2602         CHESTER CLOSE NORTH  2.450000e+06   
2633                CHEYNE COURT  2.250000e+06   
2636                  CHEYNE ROW  2.410000e+06   
2681               CHISWICK MALL  2.287500e+06   
2756                   CITY ROAD  2.468340e+06   
2803            CLARENDON STREET  2.250000e+06   
2894            CLONCURRY STREET  2.388333e+06   
2938                COLBECK MEWS  2.367500e+06   
3196       CORNWALL TERRACE MEWS  2.350000e+06   
3249          COURT LANE GARDENS  2.360000e+06   
3371              CRESCENT GROVE  2.298000e+06   
3577               DALEBURY ROAD  2.400000e+06   
3843               DEWHURST ROAD  2.425000e+06   
3924                  DORIA ROAD  2.362500e+06   
3975              DOWNSHIRE HILL  2.225000e+06   
4030                DUCHESS WALK  2.477500e+06   
4226       ECCLESTON SQUARE MEWS  2.335500e+06   
4279               EGBERT STREET  2.265000e+06   
4283               EGERTON PLACE  2.200000e+06   
4368               ELM PARK ROAD  2.320425e+06   
5006             FRANK DIXON WAY  2.212500e+06   
5088                 FULTON MEWS  2.299000e+06   
5231                 GERARD ROAD  2.258500e+06   
5234                GERRARD ROAD  2.242500e+06   
5279               GIRDLERS ROAD  2.441667e+06   
5372         GLOUCESTER CRESCENT  2.350833e+06   
5440                GORDON PLACE  2.477000e+06   
5476              GRAFTON SQUARE  2.270000e+06   
5483              GRAHAM TERRACE  2.325000e+06   
5941                HARMAN DRIVE  2.262500e+06   
5965               HARRIS STREET  2.471769e+06   
6027             HAVANNAH STREET  2.217309e+06   
6098              HAZLEWELL ROAD  2.500000e+06   
6214               HEREFORD MEWS  2.310000e+06   
6234            HERONDALE AVENUE  2.475000e+06   
6331        HIGHGATE HIGH STREET  2.211000e+06   
6346               HIGHWOOD HILL  2.252500e+06   
6382              HILLGATE PLACE  2.200000e+06   
6491           HOLLYCROFT AVENUE  2.361375e+06   
6495              HOLLYWOOD MEWS  2.350000e+06   
6541              HONEYWELL ROAD  2.278333e+06   
6597              HORTENSIA ROAD  2.275917e+06   
6626               HOXTON SQUARE  2.234286e+06   
6652                 HUNTER ROAD  2.300000e+06   
6810               JACKSONS LANE  2.362500e+06   
6870                 JOHN STREET  2.235000e+06   
7174            KINNERTON STREET  2.485600e+06   
7208         KNARESBOROUGH PLACE  2.325000e+06   
7228                 KNOX STREET  2.250000e+06   
7248              LADBROKE GROVE  2.483300e+06   
7317              LANCASTER MEWS  2.312500e+06   
7387              LANSDOWNE ROAD  2.429871e+06   
7414   LATIMER INDUSTRIAL ESTATE  2.400000e+06   
7467                LAXTON PLACE  2.500000e+06   
7666              LINCOLN 

In [14]:
df = df_affordable.drop(columns=['city_coord'])


address = 'London, UK'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London City are {}, {}.'.format(latitude, longitude))

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:6: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.


The geograpical coordinate of London City are 51.4893335, -0.144055084527687.


In [15]:
# create map of London using latitude and longitude values
map_london = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, price, street in zip(df['Latitude'], df['Longitude'], df['Avg_Price'], df['Street']):
    label = '{}, {}'.format(street, price)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

In [16]:
CLIENT_ID = 'C0UVIS44Q00FMEWVRHMO0AQ1WDWNBKSKD15I0U1U15W4HKZE' # Foursquare ID
CLIENT_SECRET = 'LUXLWGXPH5AML2GMCD4OAI0HNU4Q1STIAWVKDDTCX1FSWJEK' # Foursquare Secret
VERSION = '20181206' # Foursquare API version

We can now proceed to the Modeling phase. We will analyze neighborhoods to recommend real estates where home buyers can make a real estate investment. We will then recommend profitable venues according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores.

#### 4.Modeling

After exploring the dataset and gaining insights into it, we are ready to use the clustering methodology to analyze real estates. We will use the k-means clustering technique as it is fast and efficient in terms of computational cost, is highly flexible to account for mutations in real estate market in London and is accurate.

In [17]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Street', 
                  'Street Latitude', 
                  'Street Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [18]:
# Run the above function on each location and create a new dataframe called location_venues and display it.
location_venues = getNearbyVenues(names=df['Street'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

ALBION SQUARE
ANHALT ROAD
ANSDELL TERRACE
APPLEGARTH ROAD
AYLESTONE AVENUE
BARONSMEAD ROAD
BEAUCLERC ROAD
BELVEDERE DRIVE
BICKENHALL STREET
BIRCHLANDS AVENUE
BRAMPTON GROVE
BRIARDALE GARDENS
BROOKWAY
BURBAGE ROAD
BURY WALK
CALLCOTT STREET
CAMPDEN HILL ROAD
CAMPION ROAD
CANNING PLACE
CARLISLE ROAD
CARLTON GARDENS
CARLYLE COURT
CHALCOT SQUARE
CHARLES LANE
CHELSEA CRESCENT
CHESTER CLOSE NORTH
CHEYNE COURT
CHEYNE ROW
CHISWICK MALL
CITY ROAD
CLARENDON STREET
CLONCURRY STREET
COLBECK MEWS
CORNWALL TERRACE MEWS
COURT LANE GARDENS
CRESCENT GROVE
DALEBURY ROAD
DEWHURST ROAD
DORIA ROAD
DOWNSHIRE HILL
DUCHESS WALK
ECCLESTON SQUARE MEWS
EGBERT STREET
EGERTON PLACE
ELM PARK ROAD
FRANK DIXON WAY
FULTON MEWS
GERARD ROAD
GERRARD ROAD
GIRDLERS ROAD
GLOUCESTER CRESCENT
GORDON PLACE
GRAFTON SQUARE
GRAHAM TERRACE
HARMAN DRIVE
HARRIS STREET
HAVANNAH STREET
HAZLEWELL ROAD
HEREFORD MEWS
HERONDALE AVENUE
HIGHGATE HIGH STREET
HIGHWOOD HILL
HILLGATE PLACE
HOLLYCROFT AVENUE
HOLLYWOOD MEWS
HONEYWELL ROAD
HORTENSI

In [19]:
location_venues


Street  Street Latitude  Street Longitude  \
0                 ALBION SQUARE       -41.273758        173.289393   
1                 ALBION SQUARE       -41.273758        173.289393   
2                 ALBION SQUARE       -41.273758        173.289393   
3                 ALBION SQUARE       -41.273758        173.289393   
4                 ALBION SQUARE       -41.273758        173.289393   
5                 ALBION SQUARE       -41.273758        173.289393   
6                 ALBION SQUARE       -41.273758        173.289393   
7                 ALBION SQUARE       -41.273758        173.289393   
8                 ALBION SQUARE       -41.273758        173.289393   
9                 ALBION SQUARE       -41.273758        173.289393   
10                ALBION SQUARE       -41.273758        173.289393   
11                ALBION SQUARE       -41.273758        173.289393   
12                ALBION SQUARE       -41.273758        173.289393   
13                ALBION SQUARE       -41.273758        173.289393   
14                ALBION SQUARE       -41.273758        173.289393   
15                ALBION SQUARE       -41.273758        173.289393   
16                ALBION SQUARE       -41.273758        173.289393   
17                ALBION SQUARE       -41.273758        173.289393   
18                ALBION SQUARE       -41.273758        173.289393   
19                ALBION SQUARE       -41.273758        173.289393   
20                ALBION SQUARE       -41.273758        173.289393   
21                ALBION SQUARE       -41.273758        173.289393   
22                ALBION SQUARE       -41.273758        173.289393   
23                ALBION SQUARE       -41.273758        173.289393   
24                ALBION SQUARE       -41.273758        173.289393   
25                ALBION SQUARE       -41.273758        173.289393   
26                ALBION SQUARE       -41.273758        173.289393   
27                ALBION SQUARE       -41.273758        173.289393   
28                ALBION SQUARE       -41.273758        173.289393   
29                  ANHALT ROAD        51.480326         -0.166761   
30                  ANHALT ROAD        51.480326         -0.166761   
31                  ANHALT ROAD        51.480326         -0.166761   
32                  ANHALT ROAD        51.480326         -0.166761   
33                  ANHALT ROAD        51.480326         -0.166761   
34                  ANHALT ROAD        51.480326         -0.166761   
35                  ANHALT ROAD        51.480326         -0.166761   
36                  ANHALT ROAD        51.480326         -0.166761   
37                  ANHALT ROAD        51.480326         -0.166761   
38                  ANHALT ROAD        51.480326         -0.166761   
39                  ANHALT ROAD        51.480326         -0.166761   
40                  ANHALT ROAD        51.480326         -0.166761   
41                  ANHALT ROAD        51.480326         -0.166761   
42                  ANHALT ROAD        51.480326         -0.166761   
43              ANSDELL TERRACE        51.499890         -0.189103   
44              ANSDELL TERRACE        51.499890         -0.189103   
45              ANSDELL TERRACE        51.499890         -0.189103   
46              ANSDELL TERRACE        51.499890         -0.189103   
47              ANSDELL TERRACE        51.499890         -0.189103   
48              ANSDELL TERRACE        51.499890         -0.189103   
49              ANSDELL TERRACE        51.499890         -0.189103   
50              ANSDELL TERRACE        51.499890         -0.189103   
51              ANSDELL TERRACE        51.499890         -0.189103   
52              ANSDELL TERRACE        51.499890         -0.189103   
53              ANSDELL TERRACE        51.499890         -0.189103   
54              ANSDELL TERRACE        51.499890         -0.189103   
55              ANSDELL TERRACE        51.499890         -0.189103   
56              ANSDELL TERRACE    

In [20]:
location_venues.groupby('Street').count()


Street Latitude  Street Longitude  Venue  \
Street                                                                
ALBION SQUARE                           29                29     29   
ANHALT ROAD                             14                14     14   
ANSDELL TERRACE                         57                57     57   
APPLEGARTH ROAD                          4                 4      4   
AYLESTONE AVENUE                         4                 4      4   
BARONSMEAD ROAD                         14                14     14   
BEAUCLERC ROAD                          31                31     31   
BELVEDERE DRIVE                          2                 2      2   
BICKENHALL STREET                       97                97     97   
BIRCHLANDS AVENUE                       11                11     11   
BRAMPTON GROVE                           2                 2      2   
BRIARDALE GARDENS                        4                 4      4   
BROOKWAY                                 1                 1      1   
BURBAGE ROAD                            17                17     17   
BURY WALK                               11                11     11   
CALLCOTT STREET                         49                49     49   
CAMPDEN HILL ROAD                       51                51     51   
CAMPION ROAD                             3                 3      3   
CANNING PLACE                           92                92     92   
CARLISLE ROAD                            3                 3      3   
CARLTON GARDENS                         61                61     61   
CARLYLE COURT                            1                 1      1   
CHALCOT SQUARE                          59                59     59   
CHARLES LANE                            20                20     20   
CHESTER CLOSE NORTH                     20                20     20   
CHEYNE COURT                             2                 2      2   
CHEYNE ROW                              56                56     56   
CHISWICK MALL                            7                 7      7   
CITY ROAD                               60                60     60   
CLARENDON STREET                        61                61     61   
CLONCURRY STREET                        26                26     26   
COLBECK MEWS                           100               100    100   
CORNWALL TERRACE MEWS                   73                73     73   
COURT LANE GARDENS                      12                12     12   
CRESCENT GROVE                           1                 1      1   
DALEBURY ROAD                            5                 5      5   
DEWHURST ROAD                            1                 1      1   
DORIA ROAD                              62                62     62   
DOWNSHIRE HILL                          40                40     40   
DUCHESS WALK                           100               100    100   
ECCLESTON SQUARE MEWS                   96                96     96   
EGBERT STREET                            1                 1      1   
EGERTON PLACE                            8                 8      8   
ELM PARK ROAD                           64                64     64   
FRANK DIXON WAY                          6                 6      6   
FULTON MEWS                             88                88     88   
GERARD ROAD                              5                 5      5   
GERRARD ROAD                           100               100    100   
GIRDLERS ROAD                           37                37     37   
GORDON PLACE                            79                79     79   
GRAFTON SQUARE                          86                86     86   
GRAHAM TERRACE                          82                82     82   
HARMAN DRIVE                             6                 6      6   
HARRIS STREET                           41                41     41   
HAVANNAH STREET                         32         

In [21]:
# get the List of Unique Categories
print('There are {} uniques categories.'.format(len(location_venues['Venue Category'].unique())))

There are 349 uniques categories.


In [22]:
location_venues.shape

(5877, 7)

In [23]:
# one hot encoding
venues_onehot = pd.get_dummies(location_venues[['Venue Category']], prefix="", prefix_sep="")

# add street column back to dataframe
venues_onehot['Street'] = location_venues['Street'] 

# move street column to the first column
fixed_columns = [venues_onehot.columns[-1]] + list(venues_onehot.columns[:-1])

#fixed_columns
venues_onehot = venues_onehot[fixed_columns]

venues_onehot.head()

Street  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  ALBION SQUARE                  0               0                  0   
1  ALBION SQUARE                  0               0                  0   
2  ALBION SQUARE                  0               0                  0   
3  ALBION SQUARE                  0               0                  0   
4  ALBION SQUARE                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  \
0                 0                   0                      0   
1                 0                   0                      0   
2                 0                   0                      0   
3                 0                   0                      0   
4                 0                   0                      0   

   Austrian Restaurant  Auto Dealership  Auto Garage  BBQ Joint  Baby Store  \
0                    0                0            0          0           0   
1                    0                0            0          0           0   
2                    0                0            0          0           0   
3                    0                0            0          0           0   
4                    0                0            0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Bay  Beach  Bed & Breakfast  Beer Bar  \
0           0       0     0    1    0      0                0         0   
1           0       0     0    0    0      0                0         0   
2           0       0     0    0    0      0                0         0   
3           0       0     0    0    0      0                0         0   
4           0       0     0    0    0      0                0         0   

   Beer Garden  Beer Store  Belgian Restaurant  Bike Rental / Bike Share  \
0            0           0                   0                         0   
1            0           0                   0                         0   
2            0           0                   0                         0   
3            0           0                   0                         0   
4            0           0                   0                         0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0          0       0              0          0                 0         0   
1          0       0              0          0                 0         0   
2          0       0              0          0                 0         0   
3          0       0              0          0                 0         0   
4          0       0              0          0                 0         0   

   Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0           0                     0               0        0   
1              0           0                     0               0        0   
2              0           0                     0               0        0   
3              0           0                     0               0        0   
4              0           0                     0           

In [24]:
london_grouped = venues_onehot.groupby('Street').mean().reset_index()
london_grouped

Street  Accessories Store  Adult Boutique  \
0                ALBION SQUARE           0.000000            0.00   
1                  ANHALT ROAD           0.000000            0.00   
2              ANSDELL TERRACE           0.000000            0.00   
3              APPLEGARTH ROAD           0.000000            0.00   
4             AYLESTONE AVENUE           0.000000            0.00   
5              BARONSMEAD ROAD           0.000000            0.00   
6               BEAUCLERC ROAD           0.000000            0.00   
7              BELVEDERE DRIVE           0.000000            0.00   
8            BICKENHALL STREET           0.000000            0.00   
9            BIRCHLANDS AVENUE           0.000000            0.00   
10              BRAMPTON GROVE           0.000000            0.00   
11           BRIARDALE GARDENS           0.000000            0.00   
12                    BROOKWAY           0.000000            0.00   
13                BURBAGE ROAD           0.000000            0.00   
14                   BURY WALK           0.000000            0.00   
15             CALLCOTT STREET           0.000000            0.00   
16           CAMPDEN HILL ROAD           0.000000            0.00   
17                CAMPION ROAD           0.000000            0.00   
18               CANNING PLACE           0.000000            0.00   
19               CARLISLE ROAD           0.000000            0.00   
20             CARLTON GARDENS           0.000000            0.00   
21               CARLYLE COURT           0.000000            0.00   
22              CHALCOT SQUARE           0.000000            0.00   
23                CHARLES LANE           0.000000            0.00   
24         CHESTER CLOSE NORTH           0.000000            0.00   
25                CHEYNE COURT           0.000000            0.00   
26                  CHEYNE ROW           0.017857            0.00   
27               CHISWICK MALL           0.000000            0.00   
28                   CITY ROAD           0.000000            0.00   
29            CLARENDON STREET           0.000000            0.00   
30            CLONCURRY STREET           0.000000            0.00   
31                COLBECK MEWS           0.000000            0.00   
32       CORNWALL TERRACE MEWS           0.013699            0.00   
33          COURT LANE GARDENS           0.000000            0.00   
34              CRESCENT GROVE           0.000000            0.00   
35               DALEBURY ROAD           0.000000            0.00   
36               DEWHURST ROAD           0.000000            0.00   
37                  DORIA ROAD           0.000000            0.00   
38              DOWNSHIRE HILL           0.000000            0.00   
39                DUCHESS WALK           0.000000            0.00   
40       ECCLESTON SQUARE MEWS           0.000000            0.00   
41               EGBERT STREET           0.000000            0.00   
42               EGERTON PLACE           0.000000            0.00   
43               ELM PARK ROAD           0.015625            0.00   
44             FRANK DIXON WAY           0.000000            0.00   
45                 FULTON MEWS           0.000000            0.00   
46                 GERARD ROAD           0.000000            0.00   
47                GERRARD ROAD           0.000000            0.00   
48               GIRDLERS ROAD           0.000000            0.00   
49                GORDON PLACE           0.000000            0.00   
50              GRAFTON SQUARE           0.000000            0.00   
51              GRAHAM TERRACE           0.000000            0.00   
52                HARMAN DRIVE           0.000000            0.00   
53               HARRIS STREET           0.000000            0.00   
54             HAVANNAH STREET           0.000000            0.00   
55              HAZLEWELL ROAD           0.000000            0.00   
56               HEREFORD MEWS           0.010000            0.00   
57            HERONDAL

In [25]:
london_grouped.shape


(152, 350)

In [26]:
# What are the top 5 venues/facilities nearby profitable real estate investments?#

num_top_venues = 5

for hood in london_grouped['Street']:
    print("----"+hood+"----")
    temp = london_grouped[london_grouped['Street'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----ALBION SQUARE----
               venue  freq
0               Café  0.17
1        Coffee Shop  0.07
2  Indian Restaurant  0.07
3         Restaurant  0.07
4                Pub  0.07


----ANHALT ROAD----
                  venue  freq
0                   Pub  0.29
1         Grocery Store  0.14
2  Gym / Fitness Center  0.07
3                Garden  0.07
4                 Diner  0.07


----ANSDELL TERRACE----
                venue  freq
0      Clothing Store  0.07
1          Restaurant  0.07
2  Italian Restaurant  0.05
3                Café  0.05
4               Hotel  0.05


----APPLEGARTH ROAD----
                   venue  freq
0                    Pub  0.50
1              Nightclub  0.25
2                 Casino  0.25
3  Outdoors & Recreation  0.00
4       Pedestrian Plaza  0.00


----AYLESTONE AVENUE----
                   venue  freq
0                   Park  0.50
1          Movie Theater  0.25
2                   Café  0.25
3  Outdoors & Recreation  0.00
4  Performing Arts Venue  

In [27]:
# Define a function to return the most common venues/facilities nearby real estate investments#

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [28]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Street']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

In [29]:
# create a new dataframe
venues_sorted = pd.DataFrame(columns=columns)
venues_sorted['Street'] = london_grouped['Street']

for ind in np.arange(london_grouped.shape[0]):
    venues_sorted.iloc[ind, 1:] = return_most_common_venues(london_grouped.iloc[ind, :], num_top_venues)

In [30]:
venues_sorted.head()


Street 1st Most Common Venue 2nd Most Common Venue  \
0     ALBION SQUARE                  Café                   Pub   
1       ANHALT ROAD                   Pub         Grocery Store   
2   ANSDELL TERRACE        Clothing Store            Restaurant   
3   APPLEGARTH ROAD                   Pub             Nightclub   
4  AYLESTONE AVENUE                  Park                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Bar           Coffee Shop     Indian Restaurant   
1   Japanese Restaurant                Garden  Gym / Fitness Center   
2    Italian Restaurant                  Café                 Hotel   
3                Casino                  Food        Farmers Market   
4         Movie Theater           Yoga Studio                  Food   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Restaurant          Burger Joint           Supermarket   
1                 Diner                 Plaza    English Restaurant   
2                   Pub    Chinese Restaurant     Indian Restaurant   
3  Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   
4        Farmers Market  Fast Food Restaurant   Filipino Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0    Seafood Restaurant                Brewery  
1           Pizza Place           Cocktail Bar  
2     French Restaurant                 Garden  
3           Fish Market            Flea Market  
4     Fish & Chips Shop            Fish Market

In [33]:
venues_sorted.shape


(152, 11)

In [34]:
london_grouped.shape


(152, 350)

In [35]:
london_grouped=df


After our inspection of venues/facilities/amenities nearby the most profitable real estate investments in London, we could begin by clustering properties by venues/facilities/amenities nearby.



In [37]:
from sklearn.cluster import KMeans
#Distribute in 5 Clusters

# set number of clusters
kclusters = 5

london_grouped_clustering = london_grouped.drop('Street', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(london_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:50]

array([1, 4, 2, 4, 3, 0, 1, 0, 2, 2, 1, 4, 4, 4, 1, 0, 0, 1, 4, 2, 1, 3,
       3, 4, 1, 1, 2, 4, 3, 1, 2, 4, 0, 0, 0, 3, 4, 4, 0, 2, 1, 0, 3, 2,
       3, 2, 3, 2, 2, 4], dtype=int32)

In [38]:
#Dataframe to include Clusters

london_grouped_clustering=df
london_grouped_clustering.head()

Street     Avg_Price   Latitude   Longitude
196     ALBION SQUARE  2.450000e+06 -41.273758  173.289393
391       ANHALT ROAD  2.435000e+06  51.480326   -0.166761
406   ANSDELL TERRACE  2.250000e+06  51.499890   -0.189103
421   APPLEGARTH ROAD  2.400000e+06  53.749244   -0.326780
699  AYLESTONE AVENUE  2.286667e+06  51.540916   -0.217874

In [39]:
london_grouped_clustering.shape


(160, 4)

In [40]:
df.shape


(160, 4)

In [41]:
# add clustering labels
london_grouped_clustering['Cluster Labels'] = kmeans.labels_

# merge london_grouped with london_data to add latitude/longitude for each neighborhood
london_grouped_clustering = london_grouped_clustering.join(venues_sorted.set_index('Street'), on='Street')

london_grouped_clustering.head(30) # check the last columns!

Street     Avg_Price   Latitude   Longitude  \
196         ALBION SQUARE  2.450000e+06 -41.273758  173.289393   
391           ANHALT ROAD  2.435000e+06  51.480326   -0.166761   
406       ANSDELL TERRACE  2.250000e+06  51.499890   -0.189103   
421       APPLEGARTH ROAD  2.400000e+06  53.749244   -0.326780   
699      AYLESTONE AVENUE  2.286667e+06  51.540916   -0.217874   
853       BARONSMEAD ROAD  2.375000e+06  51.477315   -0.239457   
979        BEAUCLERC ROAD  2.480000e+06  51.499577   -0.229033   
1100      BELVEDERE DRIVE  2.340000e+06  44.762842  -63.669231   
1213    BICKENHALL STREET  2.208500e+06  51.521197   -0.158934   
1251    BIRCHLANDS AVENUE  2.217000e+06  51.448394   -0.160468   
1550       BRAMPTON GROVE  2.456875e+06  51.570365   -0.283394   
1629    BRIARDALE GARDENS  2.397132e+06  51.560175   -0.195431   
1794             BROOKWAY  2.400000e+06  45.432185 -122.802812   
1911         BURBAGE ROAD  2.445000e+06  51.450967   -0.095288   
1977            BURY WALK  2.492500e+06  52.145529   -0.423593   
2064      CALLCOTT STREET  2.375000e+06  51.508350   -0.198328   
2125    CAMPDEN HILL ROAD  2.379653e+06  51.506461   -0.198896   
2132         CAMPION ROAD  2.461000e+06  52.681351    0.965439   
2155        CANNING PLACE  2.425000e+06  53.402201   -2.987260   
2222        CARLISLE ROAD  2.200000e+06  42.549099  -71.416669   
2227      CARLTON GARDENS  2.483500e+06 -37.801943  144.971970   
2239        CARLYLE COURT  2.300000e+06  41.119072  -75.061516   
2402       CHALCOT SQUARE  2.286679e+06  51.541455   -0.155265   
2480         CHARLES LANE  2.414000e+06  40.237525  -83.349229   
2558     CHELSEA CRESCENT  2.495000e+06  34.524738  -85.448539   
2602  CHESTER CLOSE NORTH  2.450000e+06  51.529205   -0.145081   
2633         CHEYNE COURT  2.250000e+06  51.599677    0.525623   
2636           CHEYNE ROW  2.410000e+06  51.483717   -0.169603   
2681        CHISWICK MALL  2.287500e+06  51.487994   -0.246605   
2756            CITY ROAD  2.468340e+06  51.528306   -0.091946   

      Cluster Labels      1st Most Common Venue       2nd Most Common Venue  \
196                1                       Café                         Pub   
391                4                        Pub               Grocery Store   
406                2             Clothing Store                  Restaurant   
421                4                        Pub                   Nightclub   
699                3                       Park                        Café   
853                0                        Pub            Community Center   
979                1                      Hotel                         Pub   
1100               0                Gas Station               Bowling Alley   
1213               2                      Hotel                 Coffee Shop   
1251               2                        Pub           French Restaurant   
1550               1  Middle Eastern Restaurant                        Lake   
1629               4        Sporting Goods Shop               Grocery Store   
1794               4                       Park                 Yoga Studio   
1911               4                       Café                 Gas Station   
1977               1                Supermarket          English Restaurant   
2064               0                        Pub                 Yoga Studio   
2125               0                        Pub                      Bakery   
2132               1               Soccer Field                    Windmill   
2155               4                Coffee Shop                       Hotel   
2222               2             Nightlife Spot                  Playground   
2227               1         Italian Restaurant                Dessert Shop   
2239               3                 Campground                 Yoga Studio   
2402               3                       Café                         Bar   
2480               4       Fast Food Restaurant          Mexican Restaurant 

In [42]:
# Create Map

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(london_grouped_clustering['Latitude'], london_grouped_clustering['Longitude'], london_grouped_clustering['Street'], london_grouped_clustering['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [43]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 0, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
853   2375000.0                   Pub      Community Center   
1100  2340000.0           Gas Station         Bowling Alley   
2064  2375000.0                   Pub           Yoga Studio   
2125  2379652.7                   Pub                Bakery   
2938  2367500.0                 Hotel                   Pub   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
853         Breakfast Spot         Movie Theater     Food & Drink Shop   
1100     Food & Drink Shop        Farmers Market  Fast Food Restaurant   
2064         Grocery Store                Bakery     Indian Restaurant   
2125           Coffee Shop           Yoga Studio         Grocery Store   
2938                  Café    Italian Restaurant           Coffee Shop   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
853              Bookstore        Farmers Market       Thai Restaurant   
1100   Filipino Restaurant     Fish & Chips Shop           Fish Market   
2064                  Park           Coffee Shop                 Hotel   
2125                Hostel                 Hotel     Indian Restaurant   
2938                Garden     Indian Restaurant            Restaurant   

     9th Most Common Venue    10th Most Common Venue  
853                   Park               Coffee Shop  
1100           Flea Market               Flower Shop  
2064              Bus Stop          Greek Restaurant  
2125        Breakfast Spot         Food & Drink Shop  
2938                   Bar  Mediterranean Restaurant

In [44]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 1, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price      1st Most Common Venue 2nd Most Common Venue  \
196   2450000.0                       Café                   Pub   
979   2480000.0                      Hotel                   Pub   
1550  2456875.0  Middle Eastern Restaurant                  Lake   
1977  2492500.0                Supermarket    English Restaurant   
2132  2461000.0               Soccer Field              Windmill   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
196                    Bar           Coffee Shop     Indian Restaurant   
979            Coffee Shop       Thai Restaurant         Grocery Store   
1550           Yoga Studio                  Food        Farmers Market   
1977        Hardware Store   Rental Car Location                   Pub   
2132                   Spa           Yoga Studio                  Farm   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
196             Restaurant          Burger Joint           Supermarket   
979               Bus Stop    Falafel Restaurant  Fast Food Restaurant   
1550  Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   
1977   American Restaurant                  Café                  Park   
2132        Farmers Market  Fast Food Restaurant   Filipino Restaurant   

     9th Most Common Venue 10th Most Common Venue  
196     Seafood Restaurant                Brewery  
979            Supermarket           Cocktail Bar  
1550           Fish Market            Flea Market  
1977           Fish Market     Falafel Restaurant  
2132     Fish & Chips Shop            Fish Market

In [45]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 2, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue       2nd Most Common Venue  \
406   2250000.0        Clothing Store                  Restaurant   
1213  2208500.0                 Hotel                 Coffee Shop   
1251  2217000.0                   Pub           French Restaurant   
2222  2200000.0        Nightlife Spot                  Playground   
2633  2250000.0             Gastropub  Construction & Landscaping   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
406     Italian Restaurant                  Café                 Hotel   
1213                  Café    Chinese Restaurant     Indian Restaurant   
1251         Train Station                Bakery               Brewery   
2222          Soccer Field           Yoga Studio                  Food   
2633           Yoga Studio     Food & Drink Shop        Farmers Market   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
406                    Pub    Chinese Restaurant     Indian Restaurant   
1213             Gastropub    Italian Restaurant            Restaurant   
1251        Breakfast Spot                  Lake           Coffee Shop   
2222        Farmers Market  Fast Food Restaurant   Filipino Restaurant   
2633  Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   

     9th Most Common Venue 10th Most Common Venue  
406      French Restaurant                 Garden  
1213           Pizza Place        Thai Restaurant  
1251    Chinese Restaurant            Yoga Studio  
2222     Fish & Chips Shop            Fish Market  
2633           Fish Market            Flea Market

In [46]:

london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 3, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
699   2.286667e+06                  Park                  Café   
2239  2.300000e+06            Campground           Yoga Studio   
2402  2.286679e+06                  Café                   Bar   
2681  2.287500e+06                   Pub               Brewery   
3371  2.298000e+06                 Hotel           Yoga Studio   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
699          Movie Theater           Yoga Studio                  Food   
2239        Farmers Market  Fast Food Restaurant   Filipino Restaurant   
2402    Italian Restaurant                   Pub           Pizza Place   
2681             Gift Shop            Art Museum  Gym / Fitness Center   
3371               Factory                  Farm        Farmers Market   

     6th Most Common Venue          7th Most Common Venue  \
699         Farmers Market           Fast Food Restaurant   
2239     Fish & Chips Shop                    Fish Market   
2402           Coffee Shop  Vegetarian / Vegan Restaurant   
2681           Yoga Studio              Food & Drink Shop   
3371  Fast Food Restaurant            Filipino Restaurant   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
699    Filipino Restaurant     Fish & Chips Shop            Fish Market  
2239           Flea Market           Flower Shop                   Food  
2402  Fast Food Restaurant         Grocery Store            Supermarket  
2681  Fast Food Restaurant   Filipino Restaurant      Fish & Chips Shop  
3371     Fish & Chips Shop           Fish Market            Flea Market

In [47]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 4, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()


Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
391   2435000.0                   Pub         Grocery Store   
421   2400000.0                   Pub             Nightclub   
1629  2397132.0   Sporting Goods Shop         Grocery Store   
1794  2400000.0                  Park           Yoga Studio   
1911  2445000.0                  Café           Gas Station   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
391    Japanese Restaurant                Garden  Gym / Fitness Center   
421                 Casino                  Food        Farmers Market   
1629           Coffee Shop    Athletics & Sports        Farmers Market   
1794                  Food        Farmers Market  Fast Food Restaurant   
1911     Convenience Store     Fish & Chips Shop         Grocery Store   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
391                  Diner                 Plaza    English Restaurant   
421   Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   
1629  Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   
1794   Filipino Restaurant     Fish & Chips Shop           Fish Market   
1911                Bakery           Coffee Shop               Stadium   

     9th Most Common Venue 10th Most Common Venue  
391            Pizza Place           Cocktail Bar  
421            Fish Market            Flea Market  
1629           Fish Market            Flea Market  
1794           Flea Market            Flower Shop  
1911           Pizza Place     Athletics & Sports

## Results and Discussion

First of all, even though the London Housing Market may be in a rut, it is still an "ever-green" for business affairs.

We may discuss our results under two main perspectives.

First, we may examine them according to neighborhoods/London areas. It is interesting to note that, although West London (Notting Hill, Kensington, Chelsea, Marylebone) and North-West London (Hampsted) might be considered highly profitable venues to purchase a real estate according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores, South-West London (Wandsworth, Balham) and North-West London (Isliington) are arising as next future elite venues with a wide range of amenities and facilities. Accordingly, one might target under-priced real estates in these areas of London in order to make a business affair.

Second, we may analyze our results according to the five clusters we have produced. Even though, all clusters could praise an optimal range of facilities and amenities, we have found two main patterns. The first pattern we are referring to, i.e. Clusters 0, 2 and 4, may target home buyers prone to live in 'green' areas with parks, waterfronts. Instead, the second pattern we are referring to, i.e. Clusters 1 and 3, may target individuals who love pubs, theatres and soccer.



## Conclusion

To sum up, according to Bloomberg News, the London Housing Market is in a rut. It is now facing a number of different headwinds, including the prospect of higher taxes and a warning from the Bank of England that U.K. home values could fall as much as 30 percent in the event of a disorderly exit from the European Union. In this scenario, it is urgent to adopt machine learning tools in order to assist homebuyers clientele in London to make wise and effective decisions. As a result, the business problem we were posing was: how could we provide support to homebuyers clientele in to purchase a suitable real estate in London in this uncertain economic and financial scenario?

To solve this business problem, we clustered London neighborhoods in order to recommend venues and the current average price of real estate where homebuyers can make a real estate investment. We recommended profitable venues according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores.

First, we gathered data on London properties and the relative price paid data were extracted from the HM Land Registry (http://landregistry.data.gov.uk/). Moreover, to explore and target recommended locations across different venues according to the presence of amenities and essential facilities, we accessed data through FourSquare API interface and arranged them as a data frame for visualization. By merging data on London properties and the relative price paid data from the HM Land Registry and data on amenities and essential facilities surrounding such properties from FourSquare API interface, we were able to recommend profitable real estate investments.

Second, The Methodology section comprised four stages: 1. Collect Inspection Data; 2. Explore and Understand Data; 3. Data preparation and preprocessing; 4. Modeling. In particular, in the modeling section, we used the k-means clustering technique as it is fast and efficient in terms of computational cost, is highly flexible to account for mutations in real estate market in London and is accurate.

Finally, we drew the conclusion that even though the London Housing Market may be in a rut, it is still an "ever-green" for business affairs. We discussed our results under two main perspectives. First, we examined them according to neighborhoods/London areas. although West London (Notting Hill, Kensington, Chelsea, Marylebone) and North-West London (Hampsted) might be considered highly profitable venues to purchase a real estate according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores, South-West London (Wandsworth, Balham) and North-West London (Isliington) are arising as next future elite venues with a wide range of amenities and facilities. Accordingly, one might target under-priced real estates in these areas of London in order to make a business affair. Second, we analyzed our results according to the five clusters we produced. While Clusters 0, 2 and 4 may target home buyers prone to live in 'green' areas with parks, waterfronts, Clusters 1 and 3 may target individuals who love pubs, theatres and soccer.